In [ ]:
import pandas as pd
import numpy as np
import matplotlib as mpl
import matplotlib.pyplot as plt
import seaborn as sns
import warnings
warnings.filterwarnings('ignore')
from collections import OrderedDict
from time import time

import numpy as np
import scipy as sp
import pandas as pd

from scipy.optimize import fmin_powell
from scipy import integrate
from scipy import linalg

from sklearn import linear_model

sns.set_style("whitegrid")
sns.set_palette("colorblind")
palette = sns.color_palette()
figsize = (15,8)
legend_fontsize = 16

from matplotlib import rc
rc('font',**{'family':'sans-serif'})
rc('text', usetex=True)
rc('text.latex',preamble=r'\usepackage[utf8]{inputenc}')
rc('text.latex',preamble=r'\usepackage[russian]{babel}')
rc('axes', **{'titlesize': '16', 'labelsize': '16'})
rc('legend', **{'fontsize': '16'})
rc('figure', **{'dpi' : 300})

## COVID-19

In [ ]:
d = pd.read_csv("owid-covid-data-new.csv")
drus = d[d['location'] == 'Russia']
drus[drus['total_cases'] > 2].head(15)

In [ ]:
x_all = drus[drus['total_cases'] > 2]['new_cases'].to_numpy()
x_all = x_all[:60]

### uncomment if you don't have access to data
# x_all = np.array([    1,     1,     1,     1,     6,     1,     1,     1,     1,
#           15,     5,    15,    14,     4,    30,    21,    33,    52,
#           54,    53,   132,     1,    57,   163,   182,   196,   228,
#          270,   302,   501,   440,   771,   601,   582,   658,   954,
#         1154,  1175,  1459,  1786,  1667,  2186,  2558,  2774,  3388,
#         3448,  4070,  4785,  6060,  4268,  5642,  5236,  4774,  5849,
#         5966,  6361,  6198,  6411,  5841,  7099,  7933,  9623, 10633,
#        10581, 10102, 10559, 11231, 10699, 10817, 11012])

x_train = x_all[:50]
x_test = x_all[50:]
x_train[np.where(x_train == 0)] = 1

In [ ]:
plt.plot(x_all[:60])

In [ ]:
dummy_xs = np.arange(1, len(x_train)+1).reshape(-1, 1)
dummy_xs_all = np.arange(1, len(x_all)+1).reshape(-1, 1)
model = linear_model.LinearRegression(fit_intercept=True).fit( dummy_xs, np.log(x_train))

fig, ax = plt.subplots(figsize=(12,6))
ax.plot( x_all )
# plt.plot( model.predict(dummy_xs_all) )
ax.vlines(len(x_train), 0, x_all[-1], linestyle="dotted")

In [ ]:
plt.plot( np.log(x_all) )
plt.plot( model.predict(dummy_xs_all) )
plt.vlines(len(x_train), 0, 15, linestyle="dotted")

In [ ]:
np.std(model.predict(dummy_xs) - np.log(x_train))

In [ ]:
def bayesian_update(mu, sigma, x, y, sigma_noise=.25):
    x_matrix = x.reshape(1, -1)
    sigma_n = np.linalg.inv(np.linalg.inv(sigma)+ (1 / (sigma_noise ** 2)) * np.matmul(np.transpose(x_matrix), x_matrix) )
    mu_n = np.matmul(sigma_n, np.matmul(np.linalg.inv(sigma), np.transpose(mu)) + (1 / (sigma_noise ** 2)) * np.matmul(np.transpose(x_matrix), np.array([y]) ) )
    return mu_n, sigma_n

def get_poly_features(d, x):
    return np.array([ x ** i for i in range(d+1) ])

def myplot_sample_lines(ax, d, mu, sigma, xs, n=20, points=None):
    # Посэмплируем и порисуем прямые
    my_w = np.random.multivariate_normal(mu, sigma, n)

    # plt.axis('equal')
    for w in my_w:
        ax.plot(xs, np.dot(w, get_poly_features(d, xs)), 'k-', lw=.2, alpha=.5)
    if not points is None:
        ax.scatter(points[0], points[1], marker='*', s=200)

def train_poly_model(d, xs, ys, sigma_noise=.5):
    mu_0 = np.zeros(d+1)
    sigma_0 = 10 * np.identity(d+1)
    mu, sigma = mu_0, sigma_0
    for x,y in zip(xs, ys):
        mu, sigma = bayesian_update( mu, sigma, get_poly_features(d, x), y, sigma_noise=sigma_noise )
    return mu, sigma

In [ ]:
mu_0 = np.array([0, 0])
sigma_0 = np.array([[10, 0], [0, 10]])

mu, sigma = train_poly_model(1, np.arange(1, len(x_train)+1), np.log(x_train))

In [ ]:
xs=np.arange(1, len(x_all) + 1)

# Посэмплируем и порисуем прямые
fig = plt.figure(figsize=(12, 8))
ax = fig.add_subplot(111)
ax.set_xlim((xs[0], xs[-1]))
ax.set_ylim((0, 20))
myplot_sample_lines(ax, 1, mu, sigma, xs, n=20)
ax.plot(xs, np.log(x_all) )
ax.vlines(len(x_train), 0, 15, linestyle="dotted")
ax.set_ylim((0, 13))
# plt.savefig("linregr_bayes9.pdf", bbox_inches="tight")

In [ ]:
xs = np.arange(1, 100)
d = 1
n = 20

w_sample = np.random.multivariate_normal(mu, sigma, n)

fig = plt.figure(figsize=(8, 8))
ax = fig.add_subplot(111)
ax.set_xlim((xs[0], xs[-1]))
ax.set_ylim((0, 18))

for w in w_sample:
    ax.plot(xs, np.dot(w, get_poly_features(d, xs)), 'k-', lw=.2, alpha=.5)

ax.plot(xs[:len(x_all)], np.log(x_all) )
ax.vlines(len(x_train), 0, 15, linestyle="dotted")
ax.set_ylim((0, 20))
# plt.savefig("linregr_bayes9.pdf", bbox_inches="tight")

In [ ]:
mu, sigma = train_poly_model(2, np.arange(1, len(x_train)+1), np.log(x_train))

In [ ]:
xs=np.arange(1, len(x_all) + 1)

# Посэмплируем и порисуем прямые
fig = plt.figure(figsize=(12, 8))
ax = fig.add_subplot(111)
ax.set_xlim((xs[0], xs[-1]))
ax.set_ylim((0, 20))
myplot_sample_lines(ax, 2, mu, sigma, xs, n=20)
ax.plot(xs, np.log(x_all) )
ax.vlines(len(x_train), 0, 15, linestyle="dotted")
ax.set_ylim((0, 13))
# plt.savefig("linregr_bayes9.pdf", bbox_inches="tight")

In [ ]:
xs = np.arange(1, 400)
d = 2
n = 20

w_sample = np.random.multivariate_normal(mu, sigma, n)

fig = plt.figure(figsize=(12, 8))
ax = fig.add_subplot(111)
ax.set_xlim((xs[0], xs[-1]))
ax.set_ylim((0, 18))

for w in w_sample:
    ax.plot(xs, np.dot(w, get_poly_features(d, xs)), 'k-', lw=.8, alpha=.5)

ax.plot(xs[:len(x_all)], np.log(x_all) )
ax.vlines(len(x_train), 0, 15, linestyle="dotted")
ax.set_ylim((0, 20))
# plt.savefig("linregr_bayes9.pdf", bbox_inches="tight")

In [ ]:
fig = plt.figure(figsize=(10, 5))
ax = fig.add_subplot(111)
ax.set_xlim((xs[0], xs[-1]))
# ax.set_ylim((0, 18))

cumulative_predictions = np.array([ np.cumsum( np.exp(np.dot(w, get_poly_features(d, xs))) ) for w in w_sample ])

for i, w in enumerate(w_sample):
    ax.plot(xs, cumulative_predictions[i], 'k-', lw=.4)

ax.plot(xs[:len(x_all)], x_all )
ax.vlines(len(x_train), 0, 15000, linestyle="dotted")
ax.set_ylim((0, 100000000))
ax.set_xlim((0, 300))

In [ ]:
n = 100000

w_sample = np.random.multivariate_normal(mu, sigma, n)
cumulative_predictions = np.array([ np.cumsum( np.exp(np.dot(w, get_poly_features(d, xs))) ) for w in w_sample ])
total_cases = np.array([cp[-1] for cp in cumulative_predictions if cp[-1] < 100000000])

print(len(total_cases), n)

fig = plt.figure(figsize=(10, 5))
ax = fig.add_subplot(111)
ax.hist(total_cases, bins=100)
# ax.set_xlim((0, 100000000))
plt.show()

In [ ]:
np.percentile(total_cases, 90)

## Модельные методы классификации

In [ ]:
def sample_mixture(N, pi, mu1, sigma1, mu2, sigma2):
    z = np.array( np.random.rand(N) < pi, dtype=int)
    res = np.zeros((N, 2))
    res[np.where(z == 1)] = np.random.multivariate_normal(mu1, sigma1, np.sum(z))
    res[np.where(z == 0)] = np.random.multivariate_normal(mu2, sigma2, N-np.sum(z))
    return z, res

def plot_points(ax, x, z, mu1, mu2):
    ax.scatter(x[np.where(z==1), 0], x[np.where(z==1), 1], marker='.', color='b')
    ax.scatter(x[np.where(z==0), 0], x[np.where(z==0), 1], marker='.', color='r')
    ax.scatter([mu1[0]], [mu1[1]], marker='*', s=120, color='b')
    ax.scatter([mu2[0]], [mu2[1]], marker='*', s=120, color='r')


mu1, sigma1 = np.array([-1, -.5]),  np.array([[1, -.5], [-.5, 2]])
mu2, sigma2 = np.array([.5, 1]), np.array([[2, .5], [.5, .5]])
z, x = sample_mixture(100, 0.7, mu1, sigma1, mu2, sigma2)
test_z, test_x = sample_mixture(100, 0.7, mu1, sigma1, mu2, sigma2)

fig = plt.figure(figsize=(8,6))
ax = fig.add_subplot(111)
plot_points(ax, x, z, mu1, mu2)

In [ ]:
from sklearn.discriminant_analysis import LinearDiscriminantAnalysis
from sklearn.discriminant_analysis import QuadraticDiscriminantAnalysis

lda = LinearDiscriminantAnalysis(store_covariance=True)
z_lda = lda.fit(x, z).predict(x)

qda = QuadraticDiscriminantAnalysis(store_covariance=True)
z_qda = qda.fit(x, z).predict(x)

In [ ]:
from matplotlib import colors
cmap = colors.LinearSegmentedColormap(
    'red_blue_classes',
    {'red': [(0, 1, 1), (1, 0.7, 0.7)],
     'green': [(0, 0.7, 0.7), (1, 0.7, 0.7)],
     'blue': [(0, 0.7, 0.7), (1, 1, 1)]})

def plot_ellipse(ax, mu, sigma, color):
    v, w = sp.linalg.eigh(sigma)
    u = w[0] / sp.linalg.norm(w[0])
    angle = np.arctan(u[1] / u[0])
    angle = 180 * angle / np.pi
    ell = mpl.patches.Ellipse(mu, 2 * v[0] ** 0.5, 2 * v[1] ** 0.5,
                              angle=180 + angle, facecolor=color,
                              edgecolor='black', linewidth=2)
    ell.set_clip_box(ax.bbox)
    ell.set_alpha(0.2)
    ax.add_artist(ell)
    ax.scatter(mu[0], mu[1], marker='+', color=color, s=100)

def plot_colormesh(ax, model):
    nx, ny = 100, 100
    x_min, x_max = plt.xlim()
    y_min, y_max = plt.ylim()
    xx, yy = np.meshgrid(np.linspace(x_min, x_max, nx), np.linspace(y_min, y_max, ny))
    Z = model.predict_proba(np.c_[xx.ravel(), yy.ravel()])
    Z = Z[:, 1].reshape(xx.shape)
    plt.pcolormesh(xx, yy, Z, cmap=cmap,
                   norm=colors.Normalize(0., 1.), zorder=0)
    plt.contour(xx, yy, Z, [0.5], linewidths=2., colors='white')    
    plt.contour(xx, yy, Z, [0.2, 0.4, 0.6, 0.8], linewidths=.8, colors='white')    

In [ ]:
print("LDA priors: %s" % lda.priors_)

fig = plt.figure(figsize=(8,6))
ax = fig.add_subplot(111)
plot_points(ax, x, z, mu1, mu2)
plot_ellipse(ax, lda.means_[0], lda.covariance_, 'r')
plot_ellipse(ax, lda.means_[1], lda.covariance_, 'b')
plot_colormesh(ax, lda)
plt.show()

In [ ]:
print("QDA priors: %s" % qda.priors_)

fig = plt.figure(figsize=(8,6))
ax = fig.add_subplot(111)
plot_points(ax, x, z, mu1, mu2)
plot_ellipse(ax, qda.means_[0], qda.covariance_[0], 'r')
plot_ellipse(ax, qda.means_[1], qda.covariance_[1], 'b')
plot_colormesh(ax, qda)
plt.show()

## Логистическая регрессия

In [ ]:
logregr = linear_model.LogisticRegression()
z_logregr = logregr.fit(x, z).predict(x)

In [ ]:
fig = plt.figure(figsize=(8,6))
ax = fig.add_subplot(111)
plot_points(ax, x, z, mu1, mu2)
plot_colormesh(ax, logregr)
plt.show()

In [ ]:
def plot_decision_boundary(ax, model, color, label):
    nx, ny = 100, 100
    x_min, x_max = plt.xlim()
    y_min, y_max = plt.ylim()
    xx, yy = np.meshgrid(np.linspace(x_min, x_max, nx), np.linspace(y_min, y_max, ny))
    Z = model.predict_proba(np.c_[xx.ravel(), yy.ravel()])
    Z = Z[:, 1].reshape(xx.shape)
    p = ax.contour(xx, yy, Z, [0.5], linewidths=1.5, colors=[color])
    p.collections[0].set_label(label)

fig = plt.figure(figsize=(8,6))
ax = fig.add_subplot(111)
plot_points(ax, x, z, mu1, mu2)
p = plot_decision_boundary(ax, lda, palette[0], "LDA")
plot_decision_boundary(ax, qda, palette[1], "QDA")
plot_decision_boundary(ax, logregr, palette[2], "Логистическая регрессия")
plt.legend()
plt.show()